%pip install kagglehub


In [3]:
# import kagglehub

# # Download latest version
# path = kagglehub.dataset_download("uom190346a/sleep-health-and-lifestyle-dataset")

# print("Path to dataset files:", path)


Tabular Data Classification Deep learning

Project การทำนายผลว่า มีโอกาศที่จะมีปัญหาทางสุขภาพไหมและมีโอกาศกี่% และจะมีความเสี่ยงเป็นโรคออะไร

In [4]:
%pip install ydata-profiling matplotlib xgboost


Note: you may need to restart the kernel to use updated packages.


In [5]:
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as x
import pandas as pd
from ydata_profiling import ProfileReport
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.ensemble import RandomForestClassifier


In [6]:
df = pd.read_csv("/Users/b4byf4lc0n/Downloads/Prediction_health_lifestyle/Datasets/Sleep_health_and_lifestyle_dataset.csv")
df


Person ID  Gender  Age            Occupation  Sleep Duration  \
0            1    Male   27     Software Engineer             6.1   
1            2    Male   28                Doctor             6.2   
2            3    Male   28                Doctor             6.2   
3            4    Male   28  Sales Representative             5.9   
4            5    Male   28  Sales Representative             5.9   
..         ...     ...  ...                   ...             ...   
369        370  Female   59                 Nurse             8.1   
370        371  Female   59                 Nurse             8.0   
371        372  Female   59                 Nurse             8.1   
372        373  Female   59                 Nurse             8.1   
373        374  Female   59                 Nurse             8.1   

     Quality of Sleep  Physical Activity Level  Stress Level BMI Category  \
0                   6                       42             6   Overweight   
1                   6                       60             8       Normal   
2                   6                       60             8       Normal   
3                   4                       30             8        Obese   
4                   4                       30             8        Obese   
..                ...                      ...           ...          ...   
369                 9                       75             3   Overweight   
370                 9                       75             3   Overweight   
371                 9                       75             3   Overweight   
372                 9                       75             3   Overweight   
373                 9                       75             3   Overweight   

    Blood Pressure  Heart Rate  Daily Steps Sleep Disorder  
0           126/83          77         4200            NaN  
1           125/80          75        10000            NaN  
2           125/80          75        10000            NaN  
3           140/90          85         3000    Sleep Apnea  
4           140/90          85         3000    Sleep Apnea  
..             ...         ...          ...            ...  
369         140/95          68         7000    Sleep Apnea  
370         140/95          68         7000    Sleep Apnea  
371         140/95          68         7000    Sleep Apnea  
372         140/95          68         7000    Sleep Apnea  
373         140/95          68         7000    Sleep Apnea  

[374 rows x 13 columns]

In [7]:
profiles = ProfileReport(df)
profiles


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 13/13 [00:00<00:00, 102300.10it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Clean Datasets โดยให้ NaN กลายเป็น Normal

In [8]:
df['Sleep Disorder'] = df['Sleep Disorder'].fillna('Unknown')# แทนNan ด้วย Unknown


In [9]:
df.isnull().sum()


Person ID                  0
Gender                     0
Age                        0
Occupation                 0
Sleep Duration             0
Quality of Sleep           0
Physical Activity Level    0
Stress Level               0
BMI Category               0
Blood Pressure             0
Heart Rate                 0
Daily Steps                0
Sleep Disorder             0
dtype: int64

In [10]:
df.shape


(374, 13)

In [11]:
df.columns


Index(['Person ID', 'Gender', 'Age', 'Occupation', 'Sleep Duration',
       'Quality of Sleep', 'Physical Activity Level', 'Stress Level',
       'BMI Category', 'Blood Pressure', 'Heart Rate', 'Daily Steps',
       'Sleep Disorder'],
      dtype='object')

In [12]:
df = df.drop(['Person ID'], axis=1) #ลบ Person ID ออกไป


In [13]:
df.columns


Index(['Gender', 'Age', 'Occupation', 'Sleep Duration', 'Quality of Sleep',
       'Physical Activity Level', 'Stress Level', 'BMI Category',
       'Blood Pressure', 'Heart Rate', 'Daily Steps', 'Sleep Disorder'],
      dtype='object')

In [14]:
df.dtypes


Gender                      object
Age                          int64
Occupation                  object
Sleep Duration             float64
Quality of Sleep             int64
Physical Activity Level      int64
Stress Level                 int64
BMI Category                object
Blood Pressure              object
Heart Rate                   int64
Daily Steps                  int64
Sleep Disorder              object
dtype: object

Feature Engineering

In [15]:
from sklearn.preprocessing import LabelEncoder


แปลงตัว Sleep Disorder ให้เป็น Bool และเช็คค่า

In [16]:
df["Sleep_Disorder_Code"] = df["Sleep Disorder"].map({
    "Sleep Apnea": 1,
    "Insomnia": 2,
    "Unknow": 3
}).fillna(0).astype(int)


Encoder prosonal data

In [17]:
personal_cols = ["Gender", "Occupation", "BMI Category","Blood Pressure"]


In [18]:
df_encoded = df.copy()


In [19]:
for i in personal_cols:
    label_data = LabelEncoder()
    df_encoded[f"{i}_encoded"] = label_data.fit_transform(df_encoded[i])


In [20]:
df_encoded .dtypes


Gender                      object
Age                          int64
Occupation                  object
Sleep Duration             float64
Quality of Sleep             int64
Physical Activity Level      int64
Stress Level                 int64
BMI Category                object
Blood Pressure              object
Heart Rate                   int64
Daily Steps                  int64
Sleep Disorder              object
Sleep_Disorder_Code          int64
Gender_encoded               int64
Occupation_encoded           int64
BMI Category_encoded         int64
Blood Pressure_encoded       int64
dtype: object

กำหนด feature

In [21]:
health_feature = [
    "Age" , "Sleep Duration" , "Quality of Sleep" , "Physical Activity Level" , "Stress Level" , "Heart Rate" ,"Daily Steps"
]


In [22]:
personal_cols = ["Gender_encoded", "Occupation_encoded", "BMI Category_encoded","Blood Pressure_encoded"]


รวม Prosonal feature กับ health feature

In [23]:
fuction_feature = health_feature + personal_cols


In [24]:
import seaborn as sns
from sklearn.decomposition import PCA


model Binary Classification

In [25]:
X = df_encoded[fuction_feature]
y = df_encoded["Sleep_Disorder_Code"]


สำหรับ binary class

In [26]:
X1_train, X1_test, y1_train, y1_test = train_test_split(
    X, y, test_size=0.2, random_state=42, stratify=y
    
)


model Multi-class Classification

In [27]:
df_with_disorder = df_encoded[df_encoded["Sleep_Disorder_Code"] == 1].copy()


In [28]:
X2 = df_with_disorder[fuction_feature]


In [29]:
le_disorder = LabelEncoder()
y2 = le_disorder.fit_transform(df_with_disorder["Sleep Disorder"])


สำหรับ multi-class

In [30]:
X2_train, X2_test, y2_train, y2_test = train_test_split(
    X2, y2, test_size=0.2 , random_state=42 , stratify=y2
)


Scattor plot

### Binary Classification

using Xgboost

paremeter Xgboost 

In [31]:
xgb_binary = x.XGBClassifier(
    n_estimator = 100,
    max_depth=6,
    learning_rate=0.1,
    ramdon_state=42,
    eval_metric="logloss"
)


parameter RandomForest

In [32]:
rf_binary = RandomForestClassifier(
    n_estimators=100,
    max_depth=10,
    random_state=42
)


In [33]:
xgb_binary.fit(X1_train, y1_train)
rf_binary.fit(X1_train, y1_train)


/Users/b4byf4lc0n/Software_for_coding/anaconda3/lib/python3.12/site-packages/xgboost/training.py:183: UserWarning: [09:24:15] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:738: 
Parameters: { "n_estimator", "ramdon_state" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)


RandomForestClassifier(max_depth=10, random_state=42)

In [34]:
xgb_binary_predict = xgb_binary.predict(X1_test)
rf_binary_predict = rf_binary.predict(X1_test)


In [35]:
xgb_binary_probabilities = xgb_binary.predict_proba(X1_test)[:,1]
# rf_binary_predict = rf_binary.predict_proba(X1_test)[:,1]


In [36]:
from sklearn.metrics import roc_auc_score


In [37]:
accuracy_multi = accuracy_score(y1_test, xgb_binary_predict)
print(f"XGBoost Model Accuracy: {accuracy_multi:.4f}")


XGBoost Model Accuracy: 0.9200


In [38]:
auc_multi = roc_auc_score(y1_test, xgb_binary.predict_proba(X1_test), multi_class='ovr')
print(f"XGboost Model ROC: {auc_multi:.4f}")


XGboost Model ROC: 0.9384


In [39]:
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay, roc_curve, auc, RocCurveDisplay


Confusion Metrix

In [40]:
cm = confusion_matrix(y1_test, xgb_binary_predict)
disp = ConfusionMatrixDisplay(confusion_matrix=cm)
disp.plot(cmap="Blues")
plt.title("XGBoost Confusion Matrix")
plt.show()


/var/folders/pr/zbxg1gvj5bl_sqlh64jvkz7m0000gn/T/ipykernel_33872/29444349.py:5: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  plt.show()


ROC curve

In [41]:
y_pred_proba = xgb_binary.predict_proba(X1_test)[:, 1]  # ใช้ probability ของ class=1
fpr, tpr, thresholds = roc_curve(y1_test, y_pred_proba)
roc_auc = auc(fpr, tpr)


ValueError: multiclass format is not supported

In [43]:
plt.figure(figsize=(6, 6))
plt.plot(fpr, tpr, color="darkorange", lw=2, label=f"ROC curve (AUC = {roc_auc:.4f})")
plt.plot([0, 1], [0, 1], color="navy", lw=2, linestyle="--")
plt.xlabel("False Positive Rate")
plt.ylabel("True Positive Rate")
plt.title("Receiver Operating Characteristic (ROC) Curve")
plt.legend(loc="lower right")
plt.show()


/var/folders/pr/zbxg1gvj5bl_sqlh64jvkz7m0000gn/T/ipykernel_33872/1030114815.py:7: UserWarning: No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
  plt.legend(loc="lower right")
/var/folders/pr/zbxg1gvj5bl_sqlh64jvkz7m0000gn/T/ipykernel_33872/1030114815.py:8: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  plt.show()
